# **Bitcoin price forecasting - GBT Regressor**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



# Dependencies, Libraries and Tools

In [1]:
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "GBTRegressor"
SLOW_OPERATION = False

In [2]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [3]:
#Install some useful dependencies
import requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

from itertools import cycle

import plotly.express as px

import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import gc

import pandas as pd
import numpy as np
import json

import matplotlib.pyplot as plt
import seaborn as sns

In [4]:
# Install Spark and related dependencies
!pip install pyspark

import pyspark
from pyspark.sql import *
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark import SparkContext, SparkConf

from pyspark.ml.regression import LinearRegression, RandomForestRegressor, GBTRegressor
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation
from pyspark.ml import Pipeline

# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=f39ec10dbe26da0d66d4ea1c8e88a05ba26cb631035fd4b7dff8d5f76ea2ab2b
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


# Link to Google Drive

In [5]:
# Define GDrive paths
GDRIVE_DIR = "/content/drive"

GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"

GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_eng"

GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"

GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG


In [6]:
# Point Colaboratory to our Google Drive
from google.colab import drive

drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [7]:
# Load datasets into pyspark dataframe objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

# Import my utilities

In [26]:
import sys
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"
sys.path.append(GDRIVE_UTILITIES_DIR)

import shutil
shutil.rmtree(GDRIVE_UTILITIES_DIR + '/__pycache__')

import utilities

import importlib
importlib.reload(utilities)

<module 'utilities' from '/content/drive/MyDrive/BDC/project/utilities/utilities.py'>

# Loading features

In [9]:
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"

GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"

GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"

GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

In [10]:
# Set the target variable
TARGET_VAL = 'market-price'

# Set the features label
FEATURES_LABEL = "features"

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


# Evaluation of a simple model

In [14]:
# Get default params
params = utilities.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [20], 'maxDepth': [5], 'stepSize': [0.1]}

In [15]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_all

Model    Type      Features    Parameters         RMSE      MAPE  \
0  GBTRegressor  simple  all_features  [20, 5, 0.1]  7188.405572  0.246782   

           MAE      Variance        R2  Adjusted_R2       Time  
0  5922.464206  1.176793e+08  0.321712     0.321583  35.872992

In [16]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [17]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_more_rel

Model    Type           Features    Parameters       RMSE      MAPE  \
0  GBTRegressor  simple  more_rel_features  [20, 5, 0.1]  7975.2994  0.272084   

           MAE      Variance        R2  Adjusted_R2       Time  
0  6367.345453  1.088281e+08  0.165084     0.164925  18.064077

In [18]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [19]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_less_rel

Model    Type           Features    Parameters          RMSE  \
0  GBTRegressor  simple  less_rel_features  [20, 5, 0.1]  23865.914603   

       MAPE           MAE      Variance        R2  Adjusted_R2       Time  
0  0.981405  22115.065678  4.940417e+08 -6.476613    -6.478036  20.524689

In [20]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

# Hyperparameter tuning

In [21]:
choosen_features = more_rel_features
CHOSEN_FEATURES_LABEL = GDRIVE_MORE_REL_FEATURES_NAME

In [22]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [23]:
# Get simple params
params = utilities.get_simple_model_params(MODEL_NAME)
params

{'maxIter': [10, 20, 30],
 'maxDepth': [3, 5, 8],
 'stepSize': [0.1, 0.3, 0.5, 0.7]}

In [24]:
hyp_res = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type           Features  Proportion    Parameters  \
0  GBTRegressor  autotuning  more_rel_features         0.9  [20, 3, 0.3]   

          RMSE      MAPE         MAE      Variance        R2  Adjusted_R2  \
0  1759.057258  0.063295  1377.19269  1.293499e+07  0.853771     0.853716   

       Time  
0  7.659322

# Cross validation

In [28]:
# Get tuned params
params = utilities.get_tuned_model_params(MODEL_NAME)
params

{'maxIter': [20], 'maxDepth': [3], 'stepSize': [0.3]}

In [29]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [30]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type           Features  Splits Train&Validation  \
0  GBTRegressor  mulTs  more_rel_features       1   (21904, 21904)   
1  GBTRegressor  mulTs  more_rel_features       2   (43808, 21904)   
2  GBTRegressor  mulTs  more_rel_features       3   (65712, 21904)   
3  GBTRegressor  mulTs  more_rel_features       4   (87616, 21904)   
4  GBTRegressor  mulTs  more_rel_features       5  (109520, 21904)   

     Parameters          RMSE      MAPE           MAE      Variance        R2  \
0  [20, 3, 0.3]   6690.552686  0.694631   5341.760162  2.850837e+07 -1.746171   
1  [20, 3, 0.3]    468.179379  0.074140    386.797913  5.520118e+06  0.965126   
2  [20, 3, 0.3]   2614.276876  0.083261   1201.303631  4.381288e+06  0.540979   
3  [20, 3, 0.3]  21628.725687  0.404848  19688.270519  3.891644e+08 -4.483602   
4  [20, 3, 0.3]   4622.441463  0.192953   4064.812386  4.108399e+07  0.495994   

   Adjusted_R2      Time  
0    -1.746798  5.656236  
1     0.965118  6.250488  
2     0.540874  8.089435  
3    -4.484854  7.185451  
4     0.495879  9.572475

In [31]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type           Features  Splits Train&Validation  \
0  GBTRegressor  blkTs  more_rel_features       1    (10513, 2629)   
1  GBTRegressor  blkTs  more_rel_features       2    (10513, 2629)   
2  GBTRegressor  blkTs  more_rel_features       3    (10513, 2629)   
3  GBTRegressor  blkTs  more_rel_features       4    (10513, 2629)   
4  GBTRegressor  blkTs  more_rel_features       5    (10513, 2629)   
5  GBTRegressor  blkTs  more_rel_features       6    (10513, 2629)   
6  GBTRegressor  blkTs  more_rel_features       7    (10513, 2629)   
7  GBTRegressor  blkTs  more_rel_features       8    (10513, 2629)   
8  GBTRegressor  blkTs  more_rel_features       9    (10513, 2629)   
9  GBTRegressor  blkTs  more_rel_features      10    (10513, 2629)   

     Parameters          RMSE      MAPE           MAE      Variance        R2  \
0  [20, 3, 0.3]     17.018110  0.023983     14.268273  4.204654e+02 -0.233967   
1  [20, 3, 0.3]    895.050337  0.332880    816.001679  6.658665e+05 -4.916347   
2  [20, 3, 0.3]    480.542671  0.040972    379.553107  1.172400e+06  0.843517   
3  [20, 3, 0.3]   2095.928395  0.484553   1859.675785  3.448338e+06 -3.196611   
4  [20, 3, 0.3]    651.841162  0.050167    476.780459  2.105716e+05  0.450240   
5  [20, 3, 0.3]    296.050496  0.025926    246.503616  1.090213e+05 -0.194760   
6  [20, 3, 0.3]  16173.302703  0.283139  15044.049745  2.283089e+08 -7.598128   
7  [20, 3, 0.3]   2295.662969  0.035390   1929.835544  4.547196e+07  0.868640   
8  [20, 3, 0.3]   1029.480390  0.045104    918.621087  1.633621e+06  0.659328   
9  [20, 3, 0.3]   1563.228092  0.052701   1420.759158  1.422890e+06 -0.161935   

   Adjusted_R2      Time  
0    -0.236320  4.849786  
1    -4.927624  4.772730  
2     0.843219  4.107443  
3    -3.204611  5.742411  
4     0.449192  4.176574  
5    -0.197038  4.730270  
6    -7.614518  4.784691  
7     0.868390  4.145409  
8     0.658679  5.730498  
9    -0.164150  4.183860

# Comparison table

In [32]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [33]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model        Type           Features    Parameters          RMSE  \
0  GBTRegressor      simple       all_features  [20, 5, 0.1]   7188.405572   
0  GBTRegressor      simple  more_rel_features  [20, 5, 0.1]   7975.299400   
0  GBTRegressor      simple  less_rel_features  [20, 5, 0.1]  23865.914603   
0  GBTRegressor  autotuning  more_rel_features  [20, 3, 0.3]   1759.057258   
0  GBTRegressor       mulTs  more_rel_features  [20, 3, 0.3]   7204.835218   
0  GBTRegressor       blkTs  more_rel_features  [20, 3, 0.3]   2549.810532   

       MAPE           MAE      Variance        R2  Adjusted_R2       Time  
0  0.246782   5922.464206  1.176793e+08  0.321712     0.321583  35.872992  
0  0.272084   6367.345453  1.088281e+08  0.165084     0.164925  18.064077  
0  0.981405  22115.065678  4.940417e+08 -6.476613    -6.478036  20.524689  
0  0.063295   1377.192690  1.293499e+07  0.853771     0.853716   7.659322  
0  0.289967   6136.588922  9.373163e+07 -0.845535    -0.845956   7.350817  
0  0.137481   2310.604845  2.824440e+07 -1.348002    -1.352478   4.722367

# Training the final model

In [34]:
model = utilities.train_final_model(df, more_rel_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [35]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [36]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)